In [1]:
import csv
import Datenbank

In [2]:
# Hier werden die Nutzereingaben vorgenommen:
pfad_datenbank = r"C:\Users\fabia\OneDrive\Jade HS\Master\MGW2\Masterprojekt_allgemein\Masterprojekt\Programmierung\Campusnetz\Campusnetz.db"

In [3]:
# Es wird geprüft, ob die .db-Datei bereits vorhanden ist. Wenn dies nicht der Fall ist, wird die Datenbank mitsamt aller Tabellen angelegt.
Datenbank.Datenbank_anlegen(pfad_datenbank)

In [4]:
pfad = r"C:\Users\fabia\OneDrive\Jade HS\Master\MGW2\Masterprojekt_allgemein\Masterprojekt\Übungsnetz\Tachymeterdaten\Masterprobe_2.csv"

In [5]:
import sqlite3

liste_netzpunkte = []
liste_netzpunkte_neu = []
liste_netzpunkte_vorhanden = []
liste_zeilennummern_Orientierung = []

with open (pfad, newline='', encoding='utf-8') as csvfile:
    r = csv.reader(csvfile, delimiter=';')
    zeilennummer = 0
    for row in r:
        zeilennummer += 1
        if zeilennummer < 4:
            pass
        else:
            if row[0] != "Orientierung":
                liste_netzpunkte.append(row[0].strip())
            else:
                liste_zeilennummern_Orientierung.append(zeilennummer-1)
                liste_zeilennummern_Orientierung.append(zeilennummer)
           #print(row)


liste_netzpunkte = list(set(liste_netzpunkte))

con = sqlite3.connect(pfad_datenbank)
cursor = con.cursor()
cursor.execute("""SELECT punktnummer FROM Netzpunkte""")
liste_netzpunkte_in_db = {row[0] for row in cursor.fetchall()}

liste_netzpunkte_neu = [np for np in liste_netzpunkte if np not in liste_netzpunkte_in_db]
liste_netzpunkte_vorhanden = [np for np in liste_netzpunkte if np in liste_netzpunkte_in_db]

for np_neu in liste_netzpunkte_neu:
    cursor.execute("INSERT INTO Netzpunkte (punktnummer) VALUES (?)", (np_neu,))

with open (pfad, newline='', encoding='utf-8') as csvfile:
    r = csv.reader(csvfile, delimiter=';')
    for nummer, row in enumerate(r, start=1):
        if nummer < 4:
            pass
        if nummer in liste_zeilennummern_Orientierung:
            if row[0] != "Orientierung":
                punktnummer = row[0].strip()
            else:
                cursor.execute("INSERT INTO Standpunkte_Tachymeter (punktnummer, orientierunghz, orientierungv) VALUES (?, ?, ?)", (punktnummer, row[1], row[2]))



con.commit()
con.close()



print(f"Es wurden {len(liste_netzpunkte_neu)} neue Punkte importiert. Dies sind: {', '.join(map(str, liste_netzpunkte_neu))}")
print(f"Es sind bereits {len(liste_netzpunkte_vorhanden)} Punkte im Netz enthalten. Dies sind: {', '.join(map(str, liste_netzpunkte_vorhanden))}")

Es wurden 4 neue Punkte importiert. Dies sind: 20003, 20002v, 20001, 2n
Es sind bereits 0 Punkte im Netz enthalten. Dies sind: 
